# Analyses de la plateforme de jeux-video Steam
L'objectif est d'analyser la plateforme afin de trouver la tendance actuelle.
Le jeux de données est disponible à cette adresse : s3://full-stack-bigdata-datasets/Big_Data/Project_Steam/steam_game_output.json.

In [0]:
df = spark.read.format("json").load("s3://full-stack-bigdata-datasets/Big_Data/Project_Steam/steam_game_output.json")

In [0]:
print(df.count())
display(df.limit(1))

55691


data id List(10, List(Multi-player, Valve Anti-Cheat enabled, Online PvP, Shared/Split Screen PvP, PvP), 13990, Valve, 0, Action, https://cdn.akamai.steamstatic.com/steam/apps/10/header.jpg?t=1666823513, 999, English, French, German, Italian, Spanish - Spain, Simplified Chinese, Traditional Chinese, Korean, Counter-Strike, 5199, 10,000,000 .. 20,000,000, List(true, true, true), 201215, 999, Valve, 2000/11/1, 0, Play the world's number 1 online action game. Engage in an incredibly realistic brand of terrorist warfare in this wildly popular team-based game. Ally with teammates to complete strategic missions. Take out enemy sites. Rescue hostages. Your role affects your team's success. Your team's success affects your role., List(266, 1191, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, 5426, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, 227, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, 2784, null, null, null, null, null, null, null, null, null, null, null, null, 1607, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, 4831, null, null, null, null, null, null, null, null, null, 1707, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, 632, null, null, null, null, null, null, null, null, null, null, null, 3392, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, 131, null, null, 769, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, 881, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, 289, null, null, null, 3353, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, 614, null, null, null, null, null, null, 304, null, null, null, 1344, null, null, 1864, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, null, 1192), game, ) 10

In [0]:
df.printSchema()

root
 |-- data: struct (nullable = true)
 |    |-- appid: long (nullable = true)
 |    |-- categories: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |    |-- ccu: long (nullable = true)
 |    |-- developer: string (nullable = true)
 |    |-- discount: string (nullable = true)
 |    |-- genre: string (nullable = true)
 |    |-- header_image: string (nullable = true)
 |    |-- initialprice: string (nullable = true)
 |    |-- languages: string (nullable = true)
 |    |-- name: string (nullable = true)
 |    |-- negative: long (nullable = true)
 |    |-- owners: string (nullable = true)
 |    |-- platforms: struct (nullable = true)
 |    |    |-- linux: boolean (nullable = true)
 |    |    |-- mac: boolean (nullable = true)
 |    |    |-- windows: boolean (nullable = true)
 |    |-- positive: long (nullable = true)
 |    |-- price: string (nullable = true)
 |    |-- publisher: string (nullable = true)
 |    |-- release_date: string (nullable = true)
 |    |-

In [0]:
On remarque que le schema est imbriqué donc il faut récupérer les clés pour rendre le schema plus plats.

  File <command-3953199170249772>:1
    On remarque que le schema est imbriqué donc il faut récupérer les clés pour rendre le schema plus plats.
       ^
SyntaxError: invalid syntax


In [0]:
from pyspark.sql import functions as F

data_col = [x['name'] for x in df.schema.jsonValue()["fields"][0]["type"]["fields"]]
data_col

Out[6]: ['appid',
 'categories',
 'ccu',
 'developer',
 'discount',
 'genre',
 'header_image',
 'initialprice',
 'languages',
 'name',
 'negative',
 'owners',
 'platforms',
 'positive',
 'price',
 'publisher',
 'release_date',
 'required_age',
 'short_description',
 'tags',
 'type',
 'website']

In [0]:
from functools import reduce

# On explose le dataframe pour ne plus avoir de schema imbriqué
# et on enlève la colonne id qui est une duplication de app_id
# et data qui a été explosé
games = reduce(
  lambda new_df, col_name: new_df.withColumn(col_name, F.col(f"data.{col_name}")),
  data_col, df
).drop('id').drop('data')

games.printSchema()

root
 |-- appid: long (nullable = true)
 |-- categories: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- ccu: long (nullable = true)
 |-- developer: string (nullable = true)
 |-- discount: string (nullable = true)
 |-- genre: string (nullable = true)
 |-- header_image: string (nullable = true)
 |-- initialprice: string (nullable = true)
 |-- languages: string (nullable = true)
 |-- name: string (nullable = true)
 |-- negative: long (nullable = true)
 |-- owners: string (nullable = true)
 |-- platforms: struct (nullable = true)
 |    |-- linux: boolean (nullable = true)
 |    |-- mac: boolean (nullable = true)
 |    |-- windows: boolean (nullable = true)
 |-- positive: long (nullable = true)
 |-- price: string (nullable = true)
 |-- publisher: string (nullable = true)
 |-- release_date: string (nullable = true)
 |-- required_age: string (nullable = true)
 |-- short_description: string (nullable = true)
 |-- tags: struct (nullable = true)
 |    |-- 1980s: lon

In [0]:
Maintenant que le schema est plus lisible, on peut regarder les données plus facilement

  File <command-3953199170249773>:1
    Maintenant que le schema est plus lisible, on peut regarder les données plus facilement
               ^
SyntaxError: invalid syntax


In [0]:
import pandas as pd
pd.set_option('display.max_columns', None)
games.limit(5).toPandas()

appid 
 categories 
 ccu 
 developer 
 discount 
 genre 
 header_image 
 initialprice 
 languages 
 name 
 negative 
 owners 
 platforms 
 positive 
 price 
 publisher 
 release_date 
 required_age 
 short_description 
 tags 
 type 
 website 
 
 
 
 
 0 
 10 
 [Multi-player, Valve Anti-Cheat enabled, Onlin... 
 13990 
 Valve 
 0 
 Action 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 999 
 English, French, German, Italian, Spanish - Sp... 
 Counter-Strike 
 5199 
 10,000,000 .. 20,000,000 
 {'linux': True, 'mac': True, 'windows': True} 
 201215 
 999 
 Valve 
 2000/11/1 
 0 
 Play the world's number 1 online action game. ... 
 {'1980s': 266.0, '1990's': 1191.0, '2.5D': Non... 
 game 
 
 
 
 1 
 1000000 
 [Single-player, Partial Controller Support, St... 
 0 
 IndigoBlue Game Studio 
 0 
 Action, Adventure, Indie 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 999 
 English, Korean, Simplified Chinese 
 ASCENXION 
 5 
 0 .. 20,000 
 {'linux': False, 'mac': False, 'windows': True} 
 27 
 999 
 PsychoFlux Entertainment 
 2021/05/14 
 0 
 ASCENXION is a 2D shoot 'em up game where you ... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game 
 
 
 
 2 
 1000010 
 [Single-player, Partial Controller Support, St... 
 99 
 NEXT Studios 
 70 
 Adventure, Indie, RPG, Strategy 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 1999 
 Simplified Chinese, English, Japanese, Traditi... 
 Crown Trick 
 646 
 200,000 .. 500,000 
 {'linux': False, 'mac': False, 'windows': True} 
 4032 
 599 
 Team17, NEXT Studios 
 2020/10/16 
 0 
 Enter a labyrinth that moves as you move, wher... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game 
 
 
 
 3 
 1000030 
 [Multi-player, Single-player, Co-op, Steam Ach... 
 76 
 Vertigo Gaming Inc. 
 0 
 Action, Indie, Simulation, Strategy 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 1999 
 English 
 Cook, Serve, Delicious! 3?! 
 115 
 100,000 .. 200,000 
 {'linux': False, 'mac': True, 'windows': True} 
 1575 
 1999 
 Vertigo Gaming Inc. 
 2020/10/14 
 0 
 Cook, serve and manage your food truck as you ... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game 
 http://www.cookservedelicious.com 
 
 
 4 
 1000040 
 [Single-player] 
 0 
 DoubleC Games 
 0 
 Action, Casual, Indie, Simulation 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 199 
 Simplified Chinese 
 细胞战争 
 1 
 0 .. 20,000 
 {'linux': False, 'mac': False, 'windows': True} 
 0 
 199 
 DoubleC Games 
 2019/03/30 
 0 
 这是一款打击感十足的细胞主题游戏！操作简单但活下去却不简单，“你”作为侵入人体的细菌病毒，通... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game

In [0]:
On remarque que la date de sortie et les prix ne sont pas au bon format
Ainsi que la limite d'age qui n'est pas bien formaté ni formaté au recommendation europeéenne (3, 7, 12, 16, 18)

  File <command-3953199170249775>:1
    On remarque que la date de sortie et les prix ne sont pas au bon format
       ^
SyntaxError: invalid syntax


In [0]:
from pyspark.sql.types import IntegerType

games = games.withColumn("release_date", F.to_timestamp(F.col("release_date"), format="y/M/d"))
games = games.withColumn("initialprice", F.col("initialprice") / 100)
games = games.withColumn("price", F.col("price") / 100)
games = games.withColumn("discount", F.col("discount") / 100)
games = games.withColumn("required_age", games.required_age.cast(IntegerType()))


In [0]:
def format_required_age(data):
    if data == 13:
        return 12
    elif data == 6:
        return 7
    elif data == 20:
        return 18
    elif data == 5:
        return 7
    elif data == 15:
        return 16
    elif data == 17:
        return 18
    elif data == 9:
        return 12
    elif data == 35:
        return 3
    elif data == 8:
        return 7
    elif data == 10:
        return 12
    elif data == 14:
        return 16
    elif data == 180:
        return 18
    else:
        return data
    
format_required_age_udf = F.udf(lambda x:format_required_age(x), IntegerType()) 
games = games.withColumn("required_age", format_required_age_udf(F.col("required_age")))
games.limit(5).toPandas()

appid 
 categories 
 ccu 
 developer 
 discount 
 genre 
 header_image 
 initialprice 
 languages 
 name 
 negative 
 owners 
 platforms 
 positive 
 price 
 publisher 
 release_date 
 required_age 
 short_description 
 tags 
 type 
 website 
 
 
 
 
 0 
 10 
 [Multi-player, Valve Anti-Cheat enabled, Onlin... 
 13990 
 Valve 
 0.0 
 Action 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 9.99 
 English, French, German, Italian, Spanish - Sp... 
 Counter-Strike 
 5199 
 10,000,000 .. 20,000,000 
 {'linux': True, 'mac': True, 'windows': True} 
 201215 
 9.99 
 Valve 
 2000-11-01 
 0 
 Play the world's number 1 online action game. ... 
 {'1980s': 266.0, '1990's': 1191.0, '2.5D': Non... 
 game 
 
 
 
 1 
 1000000 
 [Single-player, Partial Controller Support, St... 
 0 
 IndigoBlue Game Studio 
 0.0 
 Action, Adventure, Indie 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 9.99 
 English, Korean, Simplified Chinese 
 ASCENXION 
 5 
 0 .. 20,000 
 {'linux': False, 'mac': False, 'windows': True} 
 27 
 9.99 
 PsychoFlux Entertainment 
 2021-05-14 
 0 
 ASCENXION is a 2D shoot 'em up game where you ... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game 
 
 
 
 2 
 1000010 
 [Single-player, Partial Controller Support, St... 
 99 
 NEXT Studios 
 0.7 
 Adventure, Indie, RPG, Strategy 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 19.99 
 Simplified Chinese, English, Japanese, Traditi... 
 Crown Trick 
 646 
 200,000 .. 500,000 
 {'linux': False, 'mac': False, 'windows': True} 
 4032 
 5.99 
 Team17, NEXT Studios 
 2020-10-16 
 0 
 Enter a labyrinth that moves as you move, wher... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game 
 
 
 
 3 
 1000030 
 [Multi-player, Single-player, Co-op, Steam Ach... 
 76 
 Vertigo Gaming Inc. 
 0.0 
 Action, Indie, Simulation, Strategy 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 19.99 
 English 
 Cook, Serve, Delicious! 3?! 
 115 
 100,000 .. 200,000 
 {'linux': False, 'mac': True, 'windows': True} 
 1575 
 19.99 
 Vertigo Gaming Inc. 
 2020-10-14 
 0 
 Cook, serve and manage your food truck as you ... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game 
 http://www.cookservedelicious.com 
 
 
 4 
 1000040 
 [Single-player] 
 0 
 DoubleC Games 
 0.0 
 Action, Casual, Indie, Simulation 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 1.99 
 Simplified Chinese 
 细胞战争 
 1 
 0 .. 20,000 
 {'linux': False, 'mac': False, 'windows': True} 
 0 
 1.99 
 DoubleC Games 
 2019-03-30 
 0 
 这是一款打击感十足的细胞主题游戏！操作简单但活下去却不简单，“你”作为侵入人体的细菌病毒，通... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game

In [0]:
games.printSchema()

root
 |-- appid: long (nullable = true)
 |-- categories: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- ccu: long (nullable = true)
 |-- developer: string (nullable = true)
 |-- discount: double (nullable = true)
 |-- genre: string (nullable = true)
 |-- header_image: string (nullable = true)
 |-- initialprice: double (nullable = true)
 |-- languages: string (nullable = true)
 |-- name: string (nullable = true)
 |-- negative: long (nullable = true)
 |-- owners: string (nullable = true)
 |-- platforms: struct (nullable = true)
 |    |-- linux: boolean (nullable = true)
 |    |-- mac: boolean (nullable = true)
 |    |-- windows: boolean (nullable = true)
 |-- positive: long (nullable = true)
 |-- price: double (nullable = true)
 |-- publisher: string (nullable = true)
 |-- release_date: timestamp (nullable = true)
 |-- required_age: integer (nullable = true)
 |-- short_description: string (nullable = true)
 |-- tags: struct (nullable = true)
 |    |-- 1980s:

In [0]:
games.describe().toPandas()

summary 
 appid 
 ccu 
 developer 
 discount 
 genre 
 header_image 
 initialprice 
 languages 
 name 
 negative 
 owners 
 positive 
 price 
 publisher 
 required_age 
 short_description 
 type 
 website 
 
 
 
 
 0 
 count 
 55691 
 55691 
 55691 
 55691 
 55691 
 55691 
 55691 
 55691 
 55691 
 55691 
 55691 
 55691 
 55691 
 55691 
 55688 
 55691 
 55691 
 55691 
 
 
 1 
 mean 
 1025603.0926720655 
 138.9596164550825 
 67392.0 
 0.026037779892621713 
 None 
 None 
 7.975663033519214 
 None 
 Infinity 
 241.8376937027527 
 None 
 1470.8755992889335 
 7.732849832104521 
 2001.0 
 0.1978882344490734 
 None 
 None 
 None 
 
 
 2 
 stddev 
 522784.96832834504 
 6002.067909130765 
 210681.70504552333 
 0.12887080174743096 
 None 
 None 
 11.047624778413402 
 None 
 NaN 
 5765.413761559615 
 None 
 30982.733479534887 
 10.931345827234507 
 1921.8937275510318 
 2.2962924614818236 
 None 
 None 
 None 
 
 
 3 
 min 
 10 
 0 
 
 0.0 
 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 0.0 
 
 Fieldrunners 2 
 0 
 0 .. 20,000 
 0 
 0.0 
 
 0 
 
 game 
 
 
 
 4 
 max 
 2190950 
 874053 
 ＼上／ 
 0.9 
 Web Publishing 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 999.0 
 Turkish 
 ～Daydream～蝶が舞う頃に 
 908515 
 500,000 .. 1,000,000 
 5943345 
 999.0 
 Ｌｅｍｏｎ　Ｂａｌｍ 
 180 
 🚗 Take part in a roller coaster of emotions wi... 
 hardware 
 www.windybeard.com

In [0]:
pd.DataFrame.from_dict(
  {c: games.filter(games[c].isNull()).count() for c in games.columns},
  orient='index', columns=['missing values']
).T

appid 
 categories 
 ccu 
 developer 
 discount 
 genre 
 header_image 
 initialprice 
 languages 
 name 
 negative 
 owners 
 platforms 
 positive 
 price 
 publisher 
 release_date 
 required_age 
 short_description 
 tags 
 type 
 website 
 
 
 
 
 missing values 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 0 
 222 
 3 
 0 
 0 
 0 
 0

In [0]:
On remarque que certaines date de sortie et d'age requis sont manquant. Pour la date de sortie ce n'est pas important, on ne les filtrera si on a besoin de cette information, ils representent seulement 0,4% du du jeu de données. Pour l'age requis vu qu'il n'y en a que 3, on peut aller rechercher cette information à la main. 

  File <command-2626139463254813>:1
    On remarque que certaines date de sortie et d'age requis sont manquant. Pour la date de sortie ce n'est pas important, on ne les filtrera si on a besoin de cette information, ils representent seulement 0,4% du du jeu de données. Pour l'age requis vu qu'il n'y en a que 3, on peut aller rechercher cette information à la main.
       ^
SyntaxError: invalid syntax


In [0]:
games.filter(games.required_age.isNull()).toPandas()

appid 
 categories 
 ccu 
 developer 
 discount 
 genre 
 header_image 
 initialprice 
 languages 
 name 
 negative 
 owners 
 platforms 
 positive 
 price 
 publisher 
 release_date 
 required_age 
 short_description 
 tags 
 type 
 website 
 
 
 
 
 0 
 1328670 
 [Single-player, Steam Achievements, Full contr... 
 2876 
 BioWare 
 0.59 
 Action, RPG 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 59.99 
 English, French, Italian, German, Spanish - Sp... 
 Mass Effect Legendary Edition 
 2058 
 500,000 .. 1,000,000 
 {'linux': False, 'mac': False, 'windows': True} 
 28834 
 24.59 
 Electronic Arts 
 2021-05-14 
 NaN 
 The Mass Effect™ Legendary Edition includes si... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game 
 https://www.ea.com/games/mass-effect/mass-effe... 
 
 
 1 
 1817140 
 [Single-player] 
 0 
 Kennedy Demir, Jonathan Demir 
 0.00 
 Action, Adventure 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 2.99 
 English 
 Ending Way 
 0 
 0 .. 20,000 
 {'linux': False, 'mac': False, 'windows': True} 
 3 
 2.99 
 Kennedy Demir, Jonathan Demir 
 2021-12-27 
 NaN 
 [Chapter 3] chapter 3 is now here waiting for ... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game 
 
 
 
 2 
 2120100 
 [Single-player] 
 0 
 Top Fun Gaming Inc. 
 0.00 
 Action, Adventure 
 https://cdn.akamai.steamstatic.com/steam/apps/... 
 4.99 
 English 
 Top Fun 10 VR 
 1 
 0 .. 20,000 
 {'linux': False, 'mac': False, 'windows': True} 
 0 
 4.99 
 Top Fun Gaming Inc. 
 2022-09-10 
 NaN 
 A virtual reality game where you explore towns... 
 {'1980s': None, '1990's': None, '2.5D': None, ... 
 game

In [0]:
1328670, Mass Effect Legendary Edition	--> 18
1817140, Ending Way	--> 18
2120100, Top Fun 10 VR --> introuvable --> 0

  File <command-2626139463254815>:1
    1328670, Mass Effect Legendary Edition	--> 18
                                          	 ^
SyntaxError: invalid syntax


In [0]:
games = games.withColumn(
    "required_age", 
    F.when(F.col("appid") == 1328670, 18).otherwise(F.col("required_age"))
)
games = games.withColumn(
    "required_age", 
    F.when(F.col("appid") == 1817140, 18).otherwise(F.col("required_age"))
)
games = games.withColumn(
    "required_age", 
    F.when(F.col("appid") == 2120100, 0).otherwise(F.col("required_age"))
)

In [0]:
on check si il ya des duplications

  File <command-2727127568853991>:1
    on check si il ya des duplications
       ^
SyntaxError: invalid syntax


In [0]:
games.groupby("appid").count().filter(F.col("count") > 1).count()

Out[35]: 0

In [0]:
Pas de doublon, on peut passer à l'analyse

  File <command-2727127568853997>:1
    Pas de doublon, on peut passer à l'analyse
        ^
SyntaxError: invalid syntax


In [0]:
## Analyse au niveau "macro"

Quel éditeur a publié le plus grand nombre de jeux sur Steam ?

  File <command-2727127568853999>:3
    Quel éditeur a publié le plus grand nombre de jeux sur Steam ?
         ^
SyntaxError: invalid syntax


In [0]:
display(
    games.filter(games["publisher"] != "")
    .groupby("publisher")
    .count()
    .sort(F.col("count"), ascending=False)
    .limit(10)
)

publisher count Big Fish Games 422 8floor 202 SEGA 165 Strategy First 151 Square Enix 141 Choice of Games 140 Sekai Project 132 HH-Games 132 Ubisoft 127 Laush Studio 126

Databricks visualization. Run in Databricks to view.

In [0]:
Quels sont les jeux les mieux notées ? 

  File <command-2727127568854002>:1
    Quels sont les jeux les mieux notées ?
          ^
SyntaxError: invalid syntax


In [0]:
games.createOrReplaceTempView('games')

# on prend que les jeux qui ont été noté +200 fois
display(
    spark.sql('''
        SELECT appid, name, round((positive / (negative + positive) * 100),1) as score_percent
        FROM games
        WHERE positive + negative > 200
        ORDER BY score_percent DESC
        LIMIT 20
    ''')
)

appid name score_percent 1176050 秘封旅行 ~ Secret Sealing Travel 100.0 790060 The Void Rains Upon Her Heart 100.0 992740 祈風 Inorikaze 100.0 858940 Flowers -Le volume sur ete- 99.9 1043240 Touhou Kishinjou ~ Double Dealing Character. 99.6 1070550 Don't Escape Trilogy 99.6 1684410 Seal World 99.6 1717770 The Upturned 99.6 1725640 Sudocats 99.6 1348180 From Frontier 99.5 1361230 Cleo - a pirate's tale 99.5 1100140 Touhou Fuujinroku ~ Mountain of Faith. 99.4 1423370 NOeSIS_羽化 99.4 1530140 Aventura Copilului Albastru și Urât 99.4 1733060 Ever Seen A Cat? 99.4 1260520 Patrick's Parabox 99.3 1129920 Tales From Off-Peak City Vol. 1 99.3 1677770 The Case of the Golden Idol 99.3 1055540 A Short Hike 99.3 431730 Aseprite 99.3

In [0]:
Y a-t-il des années où les sorties sont plus nombreuses ? 

Y a-t-il eu plus ou moins de sorties de jeux pendant le Covid, par exemple ?

  File <command-2727127568854004>:1
    Y a-t-il des années où les sorties sont plus nombreuses ?
      ^
SyntaxError: invalid syntax


In [0]:
display(
    spark.sql('''
        SELECT YEAR(release_date), count(*)
        FROM games
        WHERE release_date IS NOT NULL
        GROUP BY YEAR(release_date)
        ORDER BY YEAR(release_date)
    ''')
)

year(release_date) count(1) 1997 2 1998 1 1999 3 2000 2 2001 4 2002 1 2003 3 2004 6 2005 6 2006 61 2007 98 2008 159 2009 309 2010 281 2011 267 2012 344 2013 469 2014 1550 2015 2566 2016 4176 2017 6006 2018 7663 2019 6949 2020 8287 2021 8805 2022 7451

Databricks visualization. Run in Databricks to view.

In [0]:
Comment les prix sont-ils distribués ? 

Y a-t-il beaucoup de jeux avec une réduction ?

  File <command-2727127568854007>:1
    Comment les prix sont-ils distribués ?
            ^
SyntaxError: invalid syntax


In [0]:
# On retire les 4 jeux qui ont un prix aberrant

display(
    spark.sql('''
        SELECT price, name, 
            price - (price % 10) as range_10,
            price - (price % 5) as range_5
        FROM games
        where price < 200
    ''')
)

price name range_10 range_5 9.99 Counter-Strike 0.0 5.0 9.99 ASCENXION 0.0 5.0 5.99 Crown Trick 0.0 5.0 19.99 Cook, Serve, Delicious! 3?! 10.0 15.0 1.99 细胞战争 0.0 0.0 7.99 Zengeon 0.0 5.0 12.99 干支セトラ　陽ノ卷｜干支etc.　陽之卷 10.0 10.0 0.0 Jumping Master(跳跳大咖) 0.0 0.0 2.99 Cube Defender 0.0 0.0 13.99 Tower of Origin2-Worm's Nest 10.0 10.0 0.99 人气动漫大乱斗 0.0 0.0 16.99 Hellish Quart 10.0 15.0 0.0 SurReal Subway 0.0 0.0 0.0 Rogue Reaper 0.0 0.0 24.99 WRATH: Aeon of Ruin 20.0 20.0 4.99 Drawngeon: Dungeons of Ink and Paper 0.0 0.0 9.99 Battle Motion 0.0 5.0 6.99 The Undisputables : Online Multiplayer Shooter 0.0 5.0 0.0 The Marvellous Machine 0.0 0.0 0.0 Tactical Control 0.0 0.0 0.99 Love Hentai: Endgame 0.0 0.0 0.0 The ScreaMaze 0.0 0.0 9.99 Clam Man 0.0 5.0 2.99 Fist Of Heaven & Hell 0.0 0.0 19.99 Rotund Rebound 10.0 15.0 11.99 Urban Tale 10.0 10.0 0.99 Flex Apocalypse Racing 0.0 0.0 14.99 RogueCraft Squadron 10.0 10.0 0.99 Gachi Finder 3000 0.0 0.0 4.99 Allspace 0.0 0.0 7.99 On Target VR Darts 0.0 5.0 3.99 REPTOMOM 0.0 0.0 1.98 Zero spring episode 3 0.0 0.0 6.99 Kill Tiger 0.0 5.0 6.99 Gun Beat 0.0 5.0 1.99 雪·疑 Sknow 0.0 0.0 19.99 Glorious Companions 10.0 15.0 0.99 Koi 0.0 0.0 15.99 Kooring VR Wonderland:Mecadino's Attack 10.0 15.0 14.99 Angry Birds VR: Isle of Pigs 10.0 10.0 0.0 Master Of Secrets: Dark Europe 0.0 0.0 0.99 ROWROW 0.0 0.0 12.99 Partial Control 10.0 10.0 19.99 VR Flight Simulator New York - Cessna 10.0 15.0 0.0 SNAILS 0.0 0.0 10.99 VireFit 10.0 10.0 6.99 Next Stop 3 0.0 5.0 1.99 The Town 0.0 0.0 6.99 Tower Behind the Moon 0.0 5.0 5.99 Chronicon Apocalyptica 0.0 5.0 0.0 In Orbit 0.0 0.0 4.99 GUIDE 0.0 0.0 4.99 Grab Lab 0.0 0.0 4.99 Diggerman 0.0 0.0 9.99 Where the Bees Make Honey 0.0 5.0 9.99 The Demon Crystal 0.0 5.0 0.0 Mars Flight VR 0.0 0.0 2.99 Twisting Mower 0.0 0.0 4.99 Diamonds 0.0 0.0 0.0 Xtreme League 0.0 0.0 16.99 KUNAI 10.0 15.0 0.0 Virus Expansion 0.0 0.0 0.0 Casual Desktop Game 0.0 0.0 9.99 RoboVirus 0.0 5.0 1.99 aMAZE Valentine 0.0 0.0 1.99 Fused 0.0 0.0 0.0 There Was A Dream 0.0 0.0 7.99 Zibbs - Alien Survival 0.0 5.0 8.99 Rhythmy 0.0 5.0 12.99 Archeo: Shinar 10.0 10.0 3.99 WARED 0.0 0.0 0.99 Rag Doll Kung Fu 0.0 0.0 14.99 SPITLINGS 10.0 10.0 0.0 INTERPOINT 0.0 0.0 0.99 Hentai beautiful girls 0.0 0.0 14.99 Negligee: Love Stories (all ages) 10.0 10.0 0.99 AUSSIE BATTLER TANKS 0.0 0.0 8.99 Vasilis 0.0 5.0 2.99 孤岛(Isolated Island) 0.0 0.0 0.0 War of Three Kingdoms 0.0 0.0 0.99 PiiSim 0.0 0.0 3.49 The Far Kingdoms: Elements 0.0 0.0 0.0 某1种青春 0.0 0.0 9.99 The Childs Sight 0.0 5.0 0.99 バグダス - デバッガー検定 - 0.0 0.0 16.99 The Five Cores Remastered 10.0 15.0 7.99 Agartha 0.0 5.0 19.99 Victory Road 10.0 15.0 7.99 Fantastic Creatures 0.0 5.0 0.0 Condors Vs Ocelots 0.0 0.0 0.99 Roulette Simulator 2 0.0 0.0 5.99 M.C.I. Escapes 0.0 5.0 4.99 The Spell - A Kinetic Novel 0.0 0.0 2.99 Eggys Games Flash Collection 0.0 0.0 9.99 HA/CK 0.0 5.0 3.99 Tiny Snow 0.0 0.0 3.99 Cell Defender 0.0 0.0 3.99 N-GON 0.0 0.0 0.0 Temple of Pizza 0.0 0.0 1.99 AWAKE - Definitive Edition 0.0 0.0 4.99 Puttin' Around 0.0 0.0 4.99 SOF - RAIDERS 0.0 0.0 0.0 Hand of Horzasha 0.0 0.0 11.99 Ordo Et Chao: New World 10.0 10.0 1.99 Tsumi 0.0 0.0 3.99 Latte Stand Tycoon 0.0 0.0 0.0 古战三国 Ancient War: Three Kingdoms 0.0 0.0 7.99 Magus Over Fool 0.0 5.0 0.0 Galaxity 0.0 0.0 9.99 Twisty Puzzle Simulator 0.0 5.0 0.0 The Last Dinner 0.0 0.0 0.0 War of Tanks: Blitzkrieg 0.0 0.0 4.99 Gravity Panda 0.0 0.0 0.99 Hentai NetWalk 0.0 0.0 2.99 Freefall 3050AD 0.0 0.0 1.99 Symploke: Legend of Gustavo Bueno (Chapter 3) 0.0 0.0 0.0 Punishment Darkness Online 0.0 0.0 0.0 Clicker Warriors 0.0 0.0 29.99 Alluna and Brie 20.0 25.0 0.99 Groomer 0.0 0.0 14.99 Through the Darkest of Times 10.0 10.0 14.99 Hitchhiker - A Mystery Game 10.0 10.0 9.99 TRANSIT 0.0 5.0 5.99 Alpacapaca Double Dash 0.0 5.0 9.99 AIRA VR 0.0 5.0 1.99 Nya Nya Nya Girls 2 (ʻʻʻ)_(=^･ω･^=)_(ʻʻʻ) 0.0 0.0 9.99 ШХД: ЗИМА / IT'S WINTER 0.0 5.0 24.99 Graywalkers: Purgatory 20.0 20.0 0.0 The Lord of the Rings: Journeys in Middle

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:
# On retire les jeux à moins de 10€

display(
    spark.sql('''
        SELECT price, name, 
            price - (price % 10) as range_10,
            price - (price % 5) as range_5
        FROM games
        where price BETWEEN 10 AND 200
    ''')
)

price name range_10 range_5 19.99 Cook, Serve, Delicious! 3?! 10.0 15.0 12.99 干支セトラ　陽ノ卷｜干支etc.　陽之卷 10.0 10.0 13.99 Tower of Origin2-Worm's Nest 10.0 10.0 16.99 Hellish Quart 10.0 15.0 24.99 WRATH: Aeon of Ruin 20.0 20.0 19.99 Rotund Rebound 10.0 15.0 11.99 Urban Tale 10.0 10.0 14.99 RogueCraft Squadron 10.0 10.0 19.99 Glorious Companions 10.0 15.0 15.99 Kooring VR Wonderland:Mecadino's Attack 10.0 15.0 14.99 Angry Birds VR: Isle of Pigs 10.0 10.0 12.99 Partial Control 10.0 10.0 19.99 VR Flight Simulator New York - Cessna 10.0 15.0 10.99 VireFit 10.0 10.0 16.99 KUNAI 10.0 15.0 12.99 Archeo: Shinar 10.0 10.0 14.99 SPITLINGS 10.0 10.0 14.99 Negligee: Love Stories (all ages) 10.0 10.0 16.99 The Five Cores Remastered 10.0 15.0 19.99 Victory Road 10.0 15.0 11.99 Ordo Et Chao: New World 10.0 10.0 29.99 Alluna and Brie 20.0 25.0 14.99 Through the Darkest of Times 10.0 10.0 14.99 Hitchhiker - A Mystery Game 10.0 10.0 24.99 Graywalkers: Purgatory 20.0 20.0 14.99 Terrorarium 10.0 10.0 14.99 Crumbling World 10.0 10.0 39.99 Tetris Effect: Connected 30.0 35.0 10.99 Aether Way 10.0 10.0 39.99 Blacksad: Under the Skin 30.0 35.0 59.99 Silo 2 50.0 55.0 16.99 Madorica Real Estate 10.0 15.0 14.99 My Island 10.0 10.0 19.99 Paper Cut Mansion 10.0 15.0 18.99 DownStream: VR Whitewater Kayaking 10.0 15.0 19.99 KungFu Kickball 10.0 15.0 12.99 Maiden and Spell 10.0 10.0 14.99 The Secret Order 7: Shadow Breach 10.0 10.0 12.99 Fabulous - Angela's True Colors 10.0 10.0 12.99 Fabulous - New York to LA 10.0 10.0 11.99 Yukinas Diary 10.0 10.0 12.99 Delicious - Emily's Road Trip 10.0 10.0 29.99 The Jackbox Party Pack 6 20.0 25.0 14.99 Star Drift Evolution 10.0 10.0 15.99 NationWar2:Chronicle 10.0 15.0 24.99 Club Soccer Director PRO 2020 20.0 20.0 14.99 KALEIDO STELLA 10.0 10.0 11.99 Muscles And Bullets 10.0 10.0 24.99 Heroes of a Broken Land 2 20.0 20.0 24.99 the LAST LETTER 20.0 20.0 59.99 EARTH DEFENSE FORCE 5 50.0 55.0 11.24 Stage of Light 10.0 10.0 14.99 Alien Shooter 2 - The Legend 10.0 10.0 10.99 Spykebots 10.0 10.0 12.99 Fairy Picturebook of Hero and Sorceress / 勇者と魔法使いとおとぎの絵本 10.0 10.0 11.99 Photographs 10.0 10.0 19.99 Armored Front: Tiger Command 10.0 15.0 11.99 Trinity.Town: Monastery | Martial Arts and Meditation 10.0 10.0 19.99 Call of Duty: World at War 10.0 15.0 59.99 SWORD ART ONLINE Alicization Lycoris 50.0 55.0 29.99 Sankaku Renai: Love Triangle Trouble 20.0 25.0 29.99 Hello, Goodbye 20.0 25.0 24.99 The Tenants 20.0 20.0 12.99 Airborn 10.0 10.0 19.99 Changeling 10.0 15.0 14.99 Nether: The Untold Chapter 10.0 10.0 11.99 Dungeon Dreams 10.0 10.0 12.99 Nomads of the Fallen Star 10.0 10.0 10.99 Border Control 10.0 10.0 14.99 Settlement Zero 10.0 10.0 19.99 Hotel R'n'R 10.0 15.0 11.99 Outliver: Redemption 10.0 10.0 39.99 Field of Glory: Empires 30.0 35.0 24.99 Bus Mechanic Simulator 20.0 20.0 19.99 Radio General 10.0 15.0 14.99 Totally Reliable Delivery Service 10.0 10.0 24.99 Ideology in Friction 20.0 20.0 19.99 Dies irae ~Interview with Kaziklu Bey~ 10.0 15.0 14.99 Detective Girl of the Steam City 10.0 10.0 19.99 Waves Of Death VR 10.0 15.0 14.99 Gunslugs 3:Rogue Tactics 10.0 10.0 34.99 Triumph in the Skies 30.0 30.0 12.99 Buoyancy 10.0 10.0 29.99 Into the Radius VR 20.0 25.0 24.99 Moons of Madness 20.0 20.0 19.99 TimeShift 10.0 15.0 44.99 Funbag Fantasy 40.0 40.0 29.99 River City Saga: Three Kingdoms 20.0 25.0 13.99 Beat Your Meat 10.0 10.0 24.99 Peaky Blinders: Mastermind 20.0 20.0 14.99 Triton Survival 10.0 10.0 14.99 Evospace 10.0 10.0 13.99 Pursuer 10.0 10.0 19.99 Draft Day Sports: College Football 2019 10.0 15.0 19.99 Draft Day Sports: College Basketball 2019 10.0 15.0 14.99 Leanna's Slice of Life 10.0 10.0 29.99 Aron's Adventure 20.0 25.0 12.99 Hotel Ever After - Ella's Wish 10.0 10.0 34.99 Hockey Manager 20|20 30.0 30.0 14.99 Markerboard Jungle: Frogs 10.0 10.0 19.99 sCATter 10.0 15.0 19.99 Prototype 10.0 15.0 11.99 Last Day of Rome 10.0 10.0 12.99 Bonds of the Skies 10.0 10.0 14.99 Sephirothic Stories 10.0 10.0 12.99 Asdivine Dios 10.0 1

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:
display(
    spark.sql('''
        SELECT 
            name,
            case
                when discount > 0 THEN TRUE
                ELSE FALSE
            END as has_discount
        FROM games
        where price > 0
    ''')
)

name has_discount Counter-Strike false ASCENXION false Crown Trick true Cook, Serve, Delicious! 3?! false 细胞战争 false Zengeon true 干支セトラ　陽ノ卷｜干支etc.　陽之卷 false Cube Defender false Tower of Origin2-Worm's Nest false 人气动漫大乱斗 false Hellish Quart false WRATH: Aeon of Ruin false Drawngeon: Dungeons of Ink and Paper false Battle Motion false The Undisputables : Online Multiplayer Shooter false Love Hentai: Endgame false Clam Man false Fist Of Heaven & Hell false Rotund Rebound false Urban Tale false Flex Apocalypse Racing false RogueCraft Squadron false Gachi Finder 3000 false Allspace false On Target VR Darts false REPTOMOM false Zero spring episode 3 false Kill Tiger false Gun Beat false 雪·疑 Sknow false Glorious Companions false Koi false Kooring VR Wonderland:Mecadino's Attack false Angry Birds VR: Isle of Pigs false ROWROW false Partial Control false VR Flight Simulator New York - Cessna false VireFit false Next Stop 3 false The Town false Tower Behind the Moon false Chronicon Apocalyptica false GUIDE false Grab Lab false Diggerman false Where the Bees Make Honey false The Demon Crystal false Twisting Mower false Diamonds false KUNAI false RoboVirus false aMAZE Valentine false Fused false Zibbs - Alien Survival false Rhythmy false Archeo: Shinar false WARED false Rag Doll Kung Fu false SPITLINGS false Hentai beautiful girls false Negligee: Love Stories (all ages) false AUSSIE BATTLER TANKS false Vasilis false 孤岛(Isolated Island) false PiiSim false The Far Kingdoms: Elements true The Childs Sight false バグダス - デバッガー検定 - false The Five Cores Remastered false Agartha false Victory Road false Fantastic Creatures false Roulette Simulator 2 false M.C.I. Escapes false The Spell - A Kinetic Novel false Eggys Games Flash Collection false HA/CK false Tiny Snow false Cell Defender false N-GON false AWAKE - Definitive Edition false Puttin' Around false SOF - RAIDERS false Ordo Et Chao: New World false Tsumi false Latte Stand Tycoon false Magus Over Fool false Twisty Puzzle Simulator false Gravity Panda false Hentai NetWalk false Freefall 3050AD false Symploke: Legend of Gustavo Bueno (Chapter 3) false Alluna and Brie false Groomer false Through the Darkest of Times false Hitchhiker - A Mystery Game false TRANSIT false Alpacapaca Double Dash false AIRA VR false Nya Nya Nya Girls 2 (ʻʻʻ)_(=^･ω･^=)_(ʻʻʻ) false ШХД: ЗИМА / IT'S WINTER false Graywalkers: Purgatory false Terrorarium false Fireboy & Watergirl: Elements false cat notebook false Hentai Crush false 学院英雄梦 HeroDreamOfSchool false Crumbling World false Tetris Effect: Connected false NashBored false Abandonment false Vacation Adventures: Park Ranger false CrossTrix false Soko Loco Deluxe false 她2 : 我还想再见到你 Her2 : I Want To See You Again false Aether Way false Dark Sun Pictures' Dark Sun - The Space Shooter false Gravity Ace false Blacksad: Under the Skin false De Profundis false Silo 2 false Card Brawl false Rhythm Overdrive false time of the zombies false Chaos Caves false Madorica Real Estate false The Truck Game false Boundary VR false Biathlon Battle VR false Pandamonia 潘德莫尼亚 false The Revenge of Johnny Bonasera: Episode 3 false Hentai Girl Karen false My Island false Maze 3D false My Exercise false Area Cooperation Economic Simulation: North Korea (ACES) false Paper Cut Mansion false Tools Up! true The Chronicles of Jonah and the Whale false DownStream: VR Whitewater Kayaking false Stickman Racer Road Draw 2 false Everpath false blocks false Find-Life EP1 false Roombo: First Blood false KungFu Kickball false Unlock Me false iDancer false WRC 8 FIA World Rally Championship true Maiden and Spell false Noel's Hope false PsyOps Solutions false The Secret Order 7: Shadow Breach false Argonauts Agency: Golden Fleece false Fabulous - Angela's True Colors false Fabulous - New York to LA false Yukinas Diary false Delicious - Emily's Road Trip false Arkane Rush Multiverse Mayhem false The Jackbox Party Pack 6 false Snake vs Snake false Anti-Grav Bamboo-copter false Star Drift Evolution false Free

Databricks visualization. Run in Databricks to view.

In [0]:
Quels sont les langues les plus représentées ? 

In [0]:
display(
    spark.sql('''
        WITH games_langs as (
            SELECT 
            explode(split(languages, ', ')) as lang
            FROM games)
        SELECT lang, count(1)
        FROM games_langs
        GROUP BY lang
        ORDER BY count(1) DESC
        LIMIT 20
    ''')
)

lang count(1) English 55116 German 14019 French 13426 Russian 12922 Simplified Chinese 12782 Spanish - Spain 12233 Japanese 10368 Italian 9304 Portuguese - Brazil 6750 Korean 6599 Traditional Chinese 6307 Polish 5375 Portuguese - Portugal 4011 Turkish 3602 Dutch 3080 Spanish - Latin America 2732 Czech 2352 Swedish 2047 Ukrainian 1928 Hungarian 1922

Databricks visualization. Run in Databricks to view.

In [0]:
Combien de jeux sont déconseillé au moins de 16/18 ans ?

In [0]:
display(
    spark.sql('''
        SELECT 
            required_age, count(1)
        FROM games
        WHERE required_age > 0
        GROUP BY required_age
    ''')
)

required_age count(1) 12 66 16 312 3 4 7 10 18 268

Databricks visualization. Run in Databricks to view.

In [0]:
## Analyse des genres

Quels genres sont les plus représentés ?

In [0]:
display(
    spark.sql('''
        WITH games_genres as (
            SELECT 
            explode(split(genre, ', ')) as genre
            FROM games)
        SELECT genre, count(1)
        FROM games_genres
        WHERE genre != ''
        GROUP BY genre
        ORDER BY count(1) DESC
    ''')
)

genre count(1) Indie 39681 Action 23759 Casual 22086 Adventure 21431 Strategy 10895 Simulation 10836 RPG 9534 Early Access 6145 Free to Play 3393 Sports 2666 Racing 2155 Massively Multiplayer 1460 Utilities 682 Design & Illustration 406 Animation & Modeling 322 Education 317 Video Production 247 Audio Production 195 Violent 168 Software Training 164 Game Development 159 Photo Editing 105 Gore 99 Web Publishing 89 Sexual Content 54 Nudity 45 Accounting 16 Movie 1

Databricks visualization. Run in Databricks to view.

In [0]:
Are there any genres that have a better positive/negative review ratio?

Do some publishers have favorite genres?

What are the most lucrative genres?

## Analyse des platformes

Are most games available on Windows/Mac/Linux instead?

Do certain genres tend to be preferentially available on certain platforms?

  File <command-2727127568853998>:3
    Are there many games prohibited for children under 16/18?
        ^
SyntaxError: invalid syntax
